In [11]:
# -*- coding: utf-8 -*-


import warnings

warnings.simplefilter('ignore')

import os
import gc
import re
import glob

import numpy as np
import pandas as pd

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 100)
from tqdm.auto import tqdm

from sklearn.preprocessing import LabelEncoder
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import TruncatedSVD
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.metrics import accuracy_score, auc, f1_score

from urllib.parse import quote, unquote, urlparse
from xgboost import XGBClassifier

In [12]:
import random


def set_seed(seed):
    random.seed(seed)
    np.random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)  # 禁止hash随机化


set_seed(2022)

In [13]:
# train

train_files = glob.glob('../data/train/*.csv')

df_train = pd.DataFrame()

for filepath in tqdm(train_files):
    df = pd.read_csv(filepath)
    df_train = pd.concat([df_train, df]).reset_index(drop=True)

df_train.fillna('__NaN__', inplace=True)

# 强迫症发作..
df_train = df_train.rename(columns={'lable': 'label'})
df_train
print(len(df_train))

100%|██████████| 6/6 [00:00<00:00,  7.64it/s]

33219


In [14]:
# label
# 0. 白
# 1. SQL 注入
# 2. 目录历遍
# 3. 远程代码执行
# 4. 命令执行
# 5. XSS 跨站脚本

In [15]:
df_test = pd.read_csv('../data/test/test.csv')
df_test.fillna('__NaN__', inplace=True)
df_test

# %%

df = pd.concat([df_train, df_test]).reset_index(drop=True)
df.shape

(37219, 7)

In [16]:
# x = df['body'][0]
# x

In [17]:
print('-------------------提取 body w2v 特征 start...------------------------')
import re

def tokenize_web(x):
    cut_chars = '[ /&]' # 必须得用[ ]围住多个分割符
    filter_chars = ['', ' ']
    token_list = re.split(cut_chars, x)
    res_list = []
    for c in token_list:
        if c not in filter_chars:
            res_list.append(c)
    return res_list

-------------------提取 body w2v 特征 start...------------------------


In [22]:
vocab = df['body'].apply(lambda x: tokenize_web(x))
vocab

0                                                [__NaN__]
1                                                [__NaN__]
2                                                [__NaN__]
3                                                [__NaN__]
4                                                [__NaN__]
                               ...                        
37214    [GET, livemsg?ad_type=WL_WK, ty=web, pu=1, ope...
37215    [GET, runtime.js, HTTP, 1.1, Host:, 121.4.111....
37216                                            [__NaN__]
37217                                            [__NaN__]
37218    [{"method":"qihoo.sdk.user.mobile.login","bizC...
Name: body, Length: 37219, dtype: object

In [23]:
vocab = vocab.tolist()

In [24]:
import numpy as np
import multiprocessing
from gensim.models.word2vec import Word2Vec
cpu_count = multiprocessing.cpu_count()
vocab_dim = 256 # 词向量对应的维度
n_iterations = 20
n_exposures = 5  # 所有频数超过10的词语
window_size = 5
# 直接词向量相加求平均
def fea_sentence(list_w):
    n0 = np.array([0. for i in range(vocab_dim)], dtype=np.float32)
    for i in list_w:
        n0 += i
    fe = n0 / len(list_w)
    fe = fe.tolist()
    return fe

def parse(data, word2vec):
    xVec = []
    for x in data:
        sentence = []
        for word in x:
            if word in word2vec:
                sentence.append(word2vec[word])
            else:  # 词不存在，则补零向量。
                sentence.append([0. for i in range(vocab_dim)])
        xVec.append(fea_sentence(sentence))

    xVec = np.array(xVec)

    return xVec


print('加载word2vec模型预测')
model = Word2Vec.load('w2v.pkl')
body_w2v_feats = parse(vocab, model.wv)

加载word2vec模型预测


In [25]:
print('body_w2v_feats.shape: ',body_w2v_feats.shape)

body_w2v_feats.shape:  (37219, 256)


[['GET',
  'livemsg?ad_type=WL_WK',
  'ty=web',
  'pu=0',
  'openudid=ed7c82fd9fe8cd29fcab434ece87b269',
  'vid=d3028h8c7mg',
  'duration=49',
  'offline=0',
  'adselector=Y',
  'from=5',
  'live=0',
  'channelId=news_news_top',
  'oadid=',
  'articleId=20191130V0F0J200',
  'adaptor=1',
  'appversion=211115',
  'l=116',
  'newnettype=1',
  'chid=2',
  'isAdVideo=false',
  'coverid=',
  'v=QNaPhoneV6.6.80',
  'pf=aphone',
  'guid=9cb7d24895913ddc0dec43f0100017e1531b',
  'step=100',
  'page=detail',
  'real_adid=',
  'requestid=e3fb4e04-70ea-49c4-ae4d-aac07a6780ac',
  'data=Ae0Rd76AFlCmTsYmAc6n0Il4waMxVP2cmpzt6%2FkWFQToZPSqL29is9rr7AEx4LMHGYU9eI57f41z3wUB%2BzR0ziREpcF%2FxEwrNqpHyM%2FPK2gTAYxDVkH1pDUy8X%2BguKkuokT3V%2FeqGAI0gv3kQVvEUAG1rbT5T83CsDWW6yI%2Fg8BWA8eqoSzVJbdHx78QHeEkwJeNX38sp9%2B01IucHHpO7RnZpqx9wUvh04uBakaqaA29T5udK1h3PT2inkATsHqkXyy38hmLMwN5ncFX8TpOAf1a6WeeNyQYkTJbF6wmkUuMvOOVjiuF3azAtiBLhJ0GnyXkuGm6non4KOVX1OPObQXxke4Fj45amLGDAD%2FjOGEl8KY2eAxhjViOrEt7gNsNZEDvqtyWAc0nVJ8arsj

In [26]:
for i in tqdm(range(vocab_dim)):
    df[f'body_w2v_{i}'] = body_w2v_feats[:, i]

100%|██████████| 256/256 [00:00<00:00, 3822.03it/s]


In [ ]:
print('-------------------提取 body w2v 特征 end...------------------------')

-------------------提取 body w2v 特征 end...------------------------


In [27]:
def get_url_query(s):
    li = re.split('[=&]', urlparse(s)[4])
    return [li[i] for i in range(len(li)) if i % 2 == 1]


def find_max_str_length(x):
    max_ = 0
    li = [len(i) for i in x]
    return max(li) if len(li) > 0 else 0


def find_str_length_std(x):
    max_ = 0
    li = [len(i) for i in x]
    return np.std(li) if len(li) > 0 else -1


df['url_unquote'] = df['url'].apply(unquote)
df['url_query'] = df['url_unquote'].apply(lambda x: get_url_query(x))
df['url_query_num'] = df['url_query'].apply(len)
df['url_query_max_len'] = df['url_query'].apply(find_max_str_length)
df['url_query_len_std'] = df['url_query'].apply(find_str_length_std)


# %%

def find_url_filetype(x):
    try:
        return re.search(r'\.[a-z]+', x).group()
    except:
        return '__NaN__'


df['url_path'] = df['url_unquote'].apply(lambda x: urlparse(x)[2])
df['url_filetype'] = df['url_path'].apply(lambda x: find_url_filetype(x))

df['url_path_len'] = df['url_path'].apply(len)
df['url_path_num'] = df['url_path'].apply(lambda x: len(re.findall('/', x)))

# %%

df['ua_short'] = df['user_agent'].apply(lambda x: x.split('/')[0])
df['ua_first'] = df['user_agent'].apply(lambda x: x.split(' ')[0])

# %%

# % % time


def add_tfidf_feats(df, col, n_components=16):
    text = list(df[col].values)
    tf = TfidfVectorizer(min_df=1,
                         analyzer='char_wb',
                         ngram_range=(1, 3),
                         stop_words='english')
    tf.fit(text)
    X = tf.transform(text)
    svd = TruncatedSVD(n_components=n_components)
    svd.fit(X)
    X_svd = svd.transform(X)
    for i in range(n_components):
        df[f'{col}_tfidf_{i}'] = X_svd[:, i]
    return df

def add_tfidf_feats_word(df, col, n_components=16):
    text = list(df[col].values)
    tf = TfidfVectorizer(min_df=1,
                         analyzer='word',
                         ngram_range=(1, 3),
                         stop_words='english')
    tf.fit(text)
    X = tf.transform(text)
    svd = TruncatedSVD(n_components=n_components)
    svd.fit(X)
    X_svd = svd.transform(X)
    for i in range(n_components):
        df[f'{col}_tfidf_word_{i}'] = X_svd[:, i]
    return df


def add_tfidf_feats_char(df, col, n_components=16):
    text = list(df[col].values)
    tf = TfidfVectorizer(min_df=1,
                         analyzer='char',
                         ngram_range=(1, 3),
                         stop_words='english')
    tf.fit(text)
    X = tf.transform(text)
    svd = TruncatedSVD(n_components=n_components)
    svd.fit(X)
    X_svd = svd.transform(X)
    for i in range(n_components):
        df[f'{col}_tfidf_char_{i}'] = X_svd[:, i]
    return df

df = add_tfidf_feats(df, 'url_unquote', n_components=256)
df = add_tfidf_feats(df, 'user_agent', n_components=256)
df = add_tfidf_feats(df, 'body', n_components=256)


df = add_tfidf_feats_word(df, 'url_unquote', n_components=256)
df = add_tfidf_feats_word(df, 'user_agent', n_components=256)
df = add_tfidf_feats_word(df, 'body', n_components=256)

df = add_tfidf_feats_char(df, 'url_unquote', n_components=256)
df = add_tfidf_feats_char(df, 'user_agent', n_components=256)
df = add_tfidf_feats_char(df, 'body', n_components=256)




In [29]:
df.to_csv('df_w2v.csv', index=False)

In [34]:
df.to_csv('df_w2v.csv', index=False)

In [43]:
import csv

In [45]:
df.to_csv('df_w2v2.csv', 
          quoting=csv.QUOTE_MINIMAL, 
          quotechar='"', 
          encoding='utf-8')

In [46]:
df1 = pd.read_csv('df_w2v2.csv')

In [53]:
df

id  method                                         user_agent  \
0       1308       2                                            __NaN__   
1       9639       2                                            __NaN__   
2      11983       2                                        Mozilla/5.0   
3      15145       2  Mozilla/5.0 (Windows NT 10.0; WOW64) AppleWebK...   
4      17463       2                                        Mozilla/4.0   
...      ...     ...                                                ...   
37214   3995       2  Dalvik/2.1.0 (Linux; U; Android 10; POT-AL00 B...   
37215   3996       2  Mozilla/5.0 (Windows NT 10.0; Win64; x64) Appl...   
37216   3997       7                                        Mozilla/4.0   
37217   3998       2                                        Wget/1.11.4   
37218   3999       7  Mozilla/5.0 (iPhone; CPU iPhone OS 13_2_3 like...   

                                                     url  refer  \
0      /cv?uuid=69c0af3ce4caa8a131e86d0a879c55d6&tc=2...     29   
1      /110/20403/stodownload?m=d5ed3ca33799d2e0588af...     29   
2      /wpsv6internet/infos.ads??v=D1S1E2&d=arMFlS7Sp...     29   
3               /dmfd/128_128_80/t01199cdfa0e3ec1bf2.jpg     29   
4      /dl1.gj.qq.com/invc/mgrdataupdate/did52_2013.0...     29   
...                                                  ...    ...   
37214  /livemsg?ad_type=WL_WK&ty=web&pu=1&openudid=64...     29   
37215                                        /runtime.js    186   
37216                                   /query?493521812     29   
37217            /stats.php?rand=JtmT4wBtrpNy5RJnNX9wCUo     29   
37218  /api/gateway.do?method=qihoo.sdk.user.mobile.l...    544   

                                                    body  label  body_w2v_0  \
0                                                __NaN__    0.0    0.000258   
1                                                __NaN__    0.0    0.000258   
2                                                __NaN__    0.0    0.000258   
3                                                __NaN__    0.0    0.000258   
4                                                __NaN__    0.0    0.000258   
...                                                  ...    ...         ...   
37214  GET /livemsg?ad_type=WL_WK&ty=web&pu=1&openudi...    NaN    0.448627   
37215  GET /runtime.js HTTP/1.1 Host: 121.4.111.58:30...    NaN   -0.216508   
37216                                            __NaN__    NaN    0.000258   
37217                                            __NaN__    NaN    0.000258   
37218  {"method":"qihoo.sdk.user.mobile.login","bizCo...    NaN    0.000000   

       body_w2v_1  body_w2v_2  body_w2v_3  body_w2v_4  body_w2v_5  body_w2v_6  \
0       -0.000474    0.000045    0.001861   -0.001579   -0.001226   -0.001827   
1       -0.000474    0.000045    0.001861   -0.001579   -0.001226   -0.001827   
2       -0.000474    0.000045    0.001861   -0.001579   -0.001226   -0.001827   
3       -0.000474    0.000045    0.001861   -0.001579   -0.001226   -0.001827   
4       -0.000474    0.000045    0.001861   -0.001579   -0.001226   -0.001827   
...           ...         ...         ...         ...         ...         ...   
37214   -0.723709   -0.369875    0.154580   -0.339852    0.219467    0.093091   
37215   -1.345902   -1.155740   -0.207384   -0.468958   -0.714763   -0.278043   
37216   -0.000474    0.000045    0.001861   -0.001579   -0.001226   -0.001827   
37217   -0.000474    0.000045    0.001861   -0.001579   -0.001226   -0.001827   
37218    0.000000    0.000000    0.000000    0.000000    0.000000    0.000000   

       body_w2v_7  body_w2v_8  body_w2v_9  body_w2v_10  body_w2v_11  \
0        0.000845    0.000800    0.000158    -0.000809     0.001045   
1        0.000845    0.000800    0.000158    -0.000809     0.001045   
2        0.000845    0.000800    0.000158    -0.000809     0.001045   
3        0.000845    0.000800    0.000158    -0.000809     0.001045   
4        0.000845    0.0008

In [33]:


# %%

for col in tqdm(['method', 'refer', 'url_filetype', 'ua_short', 'ua_first']):
    le = LabelEncoder()
    df[col] = le.fit_transform(df[col])

# %%

not_use_feats = ['id', 'user_agent', 'url', 'body', 'url_unquote', 'url_query', 'url_path', 'label']
use_features = [col for col in df.columns if col not in not_use_feats]

# %%

train = df[df['label'].notna()]
test = df[df['label'].isna()]

train.shape, test.shape

# %%

NUM_CLASSES = 6
FOLDS = 5
TARGET = 'label'

import xgboost as xgb
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import accuracy_score, f1_score
import gc
import numpy as np

def run_lgb(df_train, df_test, use_features):
    target = TARGET
    oof_pred = np.zeros((len(df_train), NUM_CLASSES))
    y_pred = np.zeros((len(df_test), NUM_CLASSES))

    folds = StratifiedKFold(n_splits=FOLDS)
    for fold, (tr_ind, val_ind) in enumerate(folds.split(df_train, df_train[TARGET])):
        print(f'Fold {fold + 1}')
        x_train, x_val = df_train[use_features].iloc[tr_ind], df_train[use_features].iloc[val_ind]
        y_train, y_val = df_train[target].iloc[tr_ind], df_train[target].iloc[val_ind]

        dtrain = xgb.DMatrix(x_train, label=y_train)
        dval = xgb.DMatrix(x_val, label=y_val)
        watchlist = [(dtrain, 'train'), (dval, 'eval')]

        params = {
            'objective': 'multi:softprob',
            'num_class': NUM_CLASSES,
            'random_seed': 2022,
            'eval_metric': 'auc'
        }

        model = xgb.train(params, dtrain, num_boost_round=100, evals=watchlist, early_stopping_rounds=10, verbose_eval=10)

        oof_pred[val_ind] = model.predict(dval)
        y_pred += model.predict(xgb.DMatrix(df_test[use_features])) / folds.n_splits

        del x_train, x_val, y_train, y_val, dtrain, dval, watchlist
        gc.collect()

    return y_pred, oof_pred

y_pred, oof_pred = run_lgb(train, test, use_features)



# %%

print('acc: ', accuracy_score(y_true=df_train['label'], y_pred=np.argmax(oof_pred, axis=1)))

# %%

sub = pd.read_csv('../data/submit_example.csv')
sub['predict'] = np.argmax(y_pred, axis=1)
sub

# %%

sub['predict'].value_counts()

# %%

sub.to_csv('main2.csv', index=False)
print('f1: ', f1_score(y_true=df_train['label'], y_pred=np.argmax(oof_pred, axis=1) , average='macro'))

100%|██████████| 5/5 [00:00<00:00, 91.65it/s]


Fold 1
[0]	train-auc:0.99539	eval-auc:0.99316
[10]	train-auc:0.99983	eval-auc:0.99853
[20]	train-auc:0.99998	eval-auc:0.99915
[30]	train-auc:1.00000	eval-auc:0.99930
[40]	train-auc:1.00000	eval-auc:0.99937
[50]	train-auc:1.00000	eval-auc:0.99937
[59]	train-auc:1.00000	eval-auc:0.99936
Fold 2
[0]	train-auc:0.99471	eval-auc:0.99342
[10]	train-auc:0.99978	eval-auc:0.99913
[20]	train-auc:0.99998	eval-auc:0.99949
[30]	train-auc:1.00000	eval-auc:0.99953
[40]	train-auc:1.00000	eval-auc:0.99952
[44]	train-auc:1.00000	eval-auc:0.99952
Fold 3
[0]	train-auc:0.99529	eval-auc:0.99392
[10]	train-auc:0.99981	eval-auc:0.99883
[20]	train-auc:0.99997	eval-auc:0.99931
[30]	train-auc:1.00000	eval-auc:0.99938
[40]	train-auc:1.00000	eval-auc:0.99941
[50]	train-auc:1.00000	eval-auc:0.99941
[53]	train-auc:1.00000	eval-auc:0.99942
Fold 4
[0]	train-auc:0.99491	eval-auc:0.99407
[10]	train-auc:0.99981	eval-auc:0.99916
[20]	train-auc:0.99998	eval-auc:0.99947
[30]	train-auc:1.00000	eval-auc:0.99952
[40]	train-auc:1

In [ ]:
from lightgbm import early_stopping, log_evaluation
import lightgbm as lgb

for col in tqdm(['method', 'refer', 'url_filetype', 'ua_short', 'ua_first']):
    le = LabelEncoder()
    df[col] = le.fit_transform(df[col])

# 将问题字段加入 not_use_feats
not_use_feats = ['id', 'user_agent', 'url', 'body', 'url_unquote', 'url_query', 'url_path', 'label',
                'scheme', 'netloc', 'path', 'params', 'query', 'fragment']
use_features = [col for col in df.columns if col not in not_use_feats]

# 检查并处理剩余的 object 类型字段
for col in use_features:
    if df[col].dtype == 'object':
        print(f"Encoding column: {col}")
        le = LabelEncoder()
        df[col] = le.fit_transform(df[col])

# %%

train = df[df['label'].notna()]
test = df[df['label'].isna()]

train.shape, test.shape

# %%

NUM_CLASSES = 6
FOLDS = 5
TARGET = 'label'

from sklearn.preprocessing import label_binarize

def run_lgb(df_train, df_test, use_features):
    target = TARGET
    oof_pred = np.zeros((len(df_train), NUM_CLASSES))
    y_pred = np.zeros((len(df_test), NUM_CLASSES))

    folds = StratifiedKFold(n_splits=FOLDS)
    for fold, (tr_ind, val_ind) in enumerate(folds.split(df_train, df_train[TARGET])):
        print(f'Fold {fold + 1}')
        x_train, x_val = df_train[use_features].iloc[tr_ind], df_train[use_features].iloc[val_ind]
        y_train, y_val = df_train[target].iloc[tr_ind], df_train[target].iloc[val_ind]
        train_set = lgb.Dataset(x_train, y_train)
        val_set = lgb.Dataset(x_val, y_val)

        params = {
            'learning_rate': 0.1,
            'metric': 'multiclass',
            'objective': 'multiclass',
            'num_classes': NUM_CLASSES,
            'feature_fraction': 0.75,
            'bagging_fraction': 0.75,
            'bagging_freq': 2,
            'n_jobs': -1,
            'seed': 2022,
            'max_depth': 10,
            'num_leaves': 100,
            'lambda_l1': 0.5,
            'lambda_l2': 0.8,
            'verbose': -1
        }

        callbacks = [early_stopping(stopping_rounds=100), log_evaluation(period=100)]
        model = lgb.train(params,
                          train_set,
                          num_boost_round=500,
                          valid_sets=[train_set, val_set],
                          callbacks=callbacks)
        oof_pred[val_ind] = model.predict(x_val)
        y_pred += model.predict(df_test[use_features]) / folds.n_splits

        print("Features importance...")
        gain = model.feature_importance('gain')
        feat_imp = pd.DataFrame({'feature': model.feature_name(),
                                 'split': model.feature_importance('split'),
                                 'gain': 100 * gain / gain.sum()}).sort_values('gain', ascending=False)
        print('Top 50 features:\n', feat_imp.head(50))

        del x_train, x_val, y_train, y_val, train_set, val_set
        gc.collect()

    return y_pred, oof_pred

y_pred, oof_pred = run_lgb(train, test, use_features)
print('acc: ', accuracy_score(np.argmax(oof_pred, axis=1), df_train['label']))

# %%

sub = pd.read_csv('../data/submit_example.csv')
sub['predict'] = np.argmax(y_pred, axis=1)
sub

# %%

sub['predict'].value_counts()

# %%

sub.to_csv('w2v_lgb.csv', index=False)
print('f1: ', f1_score(np.argmax(oof_pred, axis=1), df_train['label'], average='macro'))

100%|██████████| 5/5 [00:00<00:00, 145.58it/s]


Fold 1
Training until validation scores don't improve for 100 rounds
[100]	training's multi_logloss: 0.00335005	valid_1's multi_logloss: 0.0650434
Early stopping, best iteration is:
[54]	training's multi_logloss: 0.00645786	valid_1's multi_logloss: 0.0613617
Features importance...
Top 50 features:
                         feature  split       gain
778                body_tfidf_0     57  13.734630
1803   url_unquote_tfidf_char_1     89   7.585356
1805   url_unquote_tfidf_char_3    102   6.898252
1293    user_agent_tfidf_word_3     30   4.779635
186                body_w2v_184     17   4.233061
2315          body_tfidf_char_1     28   4.133893
279        url_unquote_tfidf_13     36   3.540282
1808   url_unquote_tfidf_char_6     49   2.965637
779                body_tfidf_1     31   2.764628
1290    user_agent_tfidf_word_0     10   2.111822
1815  url_unquote_tfidf_char_13     34   1.915059
267         url_unquote_tfidf_1     85   1.767879
792               body_tfidf_14     25   1.375566


In [52]:
import pandas as pd
import numpy as np
from tqdm import tqdm
from sklearn.preprocessing import LabelEncoder
from sklearn.decomposition import PCA
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import accuracy_score, f1_score
import xgboost as xgb
import gc

# 假设df已经加载

# 对指定的类别特征进行LabelEncoding
for col in tqdm(['method', 'refer', 'url_filetype', 'ua_short', 'ua_first']):
    le = LabelEncoder()
    df[col] = le.fit_transform(df[col])

# 定义不使用的特征
not_use_feats = ['id', 'user_agent', 'url', 'body', 'url_unquote', 'url_query', 'url_path', 'label']
use_features = [col for col in df.columns if col not in not_use_feats]

# 删除缺失值比例超过50%的特征
missing_ratio = df[use_features].isnull().sum() / df.shape[0]
cols_to_drop = missing_ratio[missing_ratio > 0.5].index
use_features = list(set(use_features) - set(cols_to_drop))

# 处理缺失值
# 填充数值型特征的NaN值
numeric_features = df[use_features].select_dtypes(include=['float64', 'int64']).columns
df[numeric_features] = df[numeric_features].fillna(df[numeric_features].mean())

# 填充类别型特征的NaN值
categorical_features = df[use_features].select_dtypes(include=['object']).columns
for col in categorical_features:
    df[col] = df[col].fillna(df[col].mode()[0])

# 分割训练集和测试集
train = df[df['label'].notna()]
test = df[df['label'].isna()]

print(train.shape, test.shape)

# 设置参数
NUM_CLASSES = 6
FOLDS = 5
TARGET = 'label'

# 使用PCA降维，选择重要特征
pca = PCA(n_components=100)  # 选择100个主成分，可以根据实际情况调整
train_pca = pca.fit_transform(train[use_features])
test_pca = pca.transform(test[use_features])

# 将PCA得到的特征转换为数据框
pca_cols = [f'pca_{i}' for i in range(train_pca.shape[1])]
train_pca_df = pd.DataFrame(train_pca, columns=pca_cols)
test_pca_df = pd.DataFrame(test_pca, columns=pca_cols)

# 合并到原始数据中
train = pd.concat([train.reset_index(drop=True), train_pca_df], axis=1)
test = pd.concat([test.reset_index(drop=True), test_pca_df], axis=1)

# 使用PCA特征进行训练
use_pca_features = pca_cols

def run_xgb(df_train, df_test, use_features):
    target = TARGET
    oof_pred = np.zeros((len(df_train), NUM_CLASSES))
    y_pred = np.zeros((len(df_test), NUM_CLASSES))

    folds = StratifiedKFold(n_splits=FOLDS, shuffle=True, random_state=2022)
    for fold, (tr_ind, val_ind) in enumerate(folds.split(df_train, df_train[TARGET])):
        print(f'Fold {fold + 1}')
        x_train, x_val = df_train[use_features].iloc[tr_ind], df_train[use_features].iloc[val_ind]
        y_train, y_val = df_train[target].iloc[tr_ind], df_train[target].iloc[val_ind]

        dtrain = xgb.DMatrix(x_train, label=y_train)
        dval = xgb.DMatrix(x_val, label=y_val)
        watchlist = [(dtrain, 'train'), (dval, 'eval')]

        params = {
            'objective': 'multi:softprob',
            'num_class': NUM_CLASSES,
            'random_state': 2022,
            'eval_metric': 'mlogloss',
            'learning_rate': 0.1,  # 降低学习率
            'max_depth': 15,        # 控制树的深度
            'subsample': 0.95,      # 每棵树采样的样本比例
            'colsample_bytree': 0.95,  # 每棵树采样的特征比例
            'lambda': 1,           # L2正则化
            'alpha': 0.1          # L1正则化
        }

        model = xgb.train(params, dtrain, num_boost_round=100, evals=watchlist,
                          early_stopping_rounds=10, verbose_eval=10)

        oof_pred[val_ind] = model.predict(dval)
        y_pred += model.predict(xgb.DMatrix(df_test[use_features])) / folds.n_splits

        del x_train, x_val, y_train, y_val, dtrain, dval, watchlist
        gc.collect()

    return y_pred, oof_pred

y_pred, oof_pred = run_xgb(train, test, use_pca_features)

# 评估模型
print('acc: ', accuracy_score(y_true=train[TARGET], y_pred=np.argmax(oof_pred, axis=1)))
print('f1: ', f1_score(y_true=train[TARGET], y_pred=np.argmax(oof_pred, axis=1), average='macro'))

# 生成提交文件
sub = pd.read_csv('../data/submit_example.csv')
sub['predict'] = np.argmax(y_pred, axis=1)
sub.to_csv('main3.csv', index=False)

100%|██████████| 5/5 [00:00<00:00, 305.28it/s]


(33219, 2578) (4000, 2578)
Fold 1
[0]	train-mlogloss:1.52118	eval-mlogloss:1.52936
[10]	train-mlogloss:0.48865	eval-mlogloss:0.53368
[20]	train-mlogloss:0.19248	eval-mlogloss:0.25317
[30]	train-mlogloss:0.08253	eval-mlogloss:0.15048
[40]	train-mlogloss:0.03908	eval-mlogloss:0.11140
[50]	train-mlogloss:0.02106	eval-mlogloss:0.09541
[60]	train-mlogloss:0.01322	eval-mlogloss:0.08934
[70]	train-mlogloss:0.00948	eval-mlogloss:0.08682
[80]	train-mlogloss:0.00752	eval-mlogloss:0.08602
[90]	train-mlogloss:0.00637	eval-mlogloss:0.08548
[99]	train-mlogloss:0.00571	eval-mlogloss:0.08544
Fold 2
[0]	train-mlogloss:1.52090	eval-mlogloss:1.52953
[10]	train-mlogloss:0.48845	eval-mlogloss:0.53822
[20]	train-mlogloss:0.19233	eval-mlogloss:0.25691
[30]	train-mlogloss:0.08200	eval-mlogloss:0.15420
[40]	train-mlogloss:0.03835	eval-mlogloss:0.11536
[50]	train-mlogloss:0.02046	eval-mlogloss:0.10047
[60]	train-mlogloss:0.01264	eval-mlogloss:0.09470
[70]	train-mlogloss:0.00893	eval-mlogloss:0.09271
[80]	train-

In [54]:


# %%

for col in tqdm(['method', 'refer', 'url_filetype', 'ua_short', 'ua_first']):
    le = LabelEncoder()
    df[col] = le.fit_transform(df[col])

# %%

not_use_feats = ['id', 'user_agent', 'url', 'body', 'url_unquote', 'url_query', 'url_path', 'label']
use_features = [col for col in df.columns if col not in not_use_feats]
# 删除缺失值比例超过50%的特征
missing_ratio = df[use_features].isnull().sum() / df.shape[0]
cols_to_drop = missing_ratio[missing_ratio > 0.5].index
print('cols_to_drop: ', cols_to_drop)
use_features = list(set(use_features) - set(cols_to_drop))
# %%

train = df[df['label'].notna()]
test = df[df['label'].isna()]

train.shape, test.shape

# %%

NUM_CLASSES = 6
FOLDS = 5
TARGET = 'label'

import xgboost as xgb
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import accuracy_score, f1_score
import gc
import numpy as np

def run_lgb(df_train, df_test, use_features):
    target = TARGET
    oof_pred = np.zeros((len(df_train), NUM_CLASSES))
    y_pred = np.zeros((len(df_test), NUM_CLASSES))

    folds = StratifiedKFold(n_splits=FOLDS)
    for fold, (tr_ind, val_ind) in enumerate(folds.split(df_train, df_train[TARGET])):
        print(f'Fold {fold + 1}')
        x_train, x_val = df_train[use_features].iloc[tr_ind], df_train[use_features].iloc[val_ind]
        y_train, y_val = df_train[target].iloc[tr_ind], df_train[target].iloc[val_ind]

        dtrain = xgb.DMatrix(x_train, label=y_train)
        dval = xgb.DMatrix(x_val, label=y_val)
        watchlist = [(dtrain, 'train'), (dval, 'eval')]

        params = {
            'objective': 'multi:softprob',
            'num_class': NUM_CLASSES,
            'random_seed': 2022,
            'eval_metric': 'auc'
        }

        model = xgb.train(params, dtrain, num_boost_round=100, evals=watchlist, early_stopping_rounds=10, verbose_eval=10)

        oof_pred[val_ind] = model.predict(dval)
        y_pred += model.predict(xgb.DMatrix(df_test[use_features])) / folds.n_splits

        del x_train, x_val, y_train, y_val, dtrain, dval, watchlist
        gc.collect()

    return y_pred, oof_pred

y_pred, oof_pred = run_lgb(train, test, use_features)



# %%

print('acc: ', accuracy_score(y_true=df_train['label'], y_pred=np.argmax(oof_pred, axis=1)))

# %%

sub = pd.read_csv('../data/submit_example.csv')
sub['predict'] = np.argmax(y_pred, axis=1)
sub

# %%

sub['predict'].value_counts()

# %%

sub.to_csv('main4.csv', index=False)
print('f1: ', f1_score(y_true=df_train['label'], y_pred=np.argmax(oof_pred, axis=1) , average='macro'))

100%|██████████| 5/5 [00:00<00:00, 90.48it/s]


cols_to_drop:  Index([], dtype='object')
Fold 1
[0]	train-auc:0.99561	eval-auc:0.99302
[10]	train-auc:0.99984	eval-auc:0.99854
[20]	train-auc:0.99997	eval-auc:0.99907
[30]	train-auc:1.00000	eval-auc:0.99927
[40]	train-auc:1.00000	eval-auc:0.99931
[50]	train-auc:1.00000	eval-auc:0.99933
[56]	train-auc:1.00000	eval-auc:0.99933
Fold 2
[0]	train-auc:0.99470	eval-auc:0.99354
[10]	train-auc:0.99980	eval-auc:0.99902
[20]	train-auc:0.99998	eval-auc:0.99943
[30]	train-auc:1.00000	eval-auc:0.99950
[40]	train-auc:1.00000	eval-auc:0.99950
Fold 3
[0]	train-auc:0.99530	eval-auc:0.99399
[10]	train-auc:0.99980	eval-auc:0.99866
[20]	train-auc:0.99998	eval-auc:0.99929
[30]	train-auc:1.00000	eval-auc:0.99934
[40]	train-auc:1.00000	eval-auc:0.99941
[50]	train-auc:1.00000	eval-auc:0.99943
[60]	train-auc:1.00000	eval-auc:0.99943
[64]	train-auc:1.00000	eval-auc:0.99943
Fold 4
[0]	train-auc:0.99498	eval-auc:0.99408
[10]	train-auc:0.99981	eval-auc:0.99910
[20]	train-auc:0.99998	eval-auc:0.99942
[30]	train-auc: